# Market Cap

- load coinmarketcap data 
- create an crypto equivalent of "stocks" with marketcap, IPO, sector 



In [68]:
import time
import random
import pandas as pd
from tqdm import tqdm
from pycoingecko import CoinGeckoAPI
cg = CoinGeckoAPI()
import numpy as np

In [69]:
# get top 100 coins from coingecko 

top_100_coins = cg.get_coins_markets(vs_currency='usd')

top_100_coins_df = pd.DataFrame(top_100_coins)
top_100_coins_df.set_index('id',inplace=True)
col_list = ['market_cap', ]
top_100_coins_df = top_100_coins_df.loc[:, col_list]

top_100_coins_list = top_100_coins_df.index.tolist()


top_100_coins_df

market_cap
id                        
bitcoin       682679851722
ethereum      300095281756
tether         62504685844
cardano        56026875934
binancecoin    54658248672
...                    ...
xsushi           848747970
husd             837090807
pirate-chain     822543502
siacoin          820073407
uma              813598380

[100 rows x 1 columns]

In [70]:
# for each coin id get detailed information and store it into a market_df

market = []
raw_data = []
for idx in tqdm(top_100_coins_list):
    coin = cg.get_coin_by_id(id=idx, localization=False, vs_currencies='usd',include_market_cap=False,
                             include_24hr_vol=False,include_24hr_change=False,include_last_updated_at=False)
    raw_data.append(coin)
    coin_info = [idx]
    coin_info.append(coin['symbol'])
    coin_info.append(str(coin['name']))
    symbol = coin['symbol']
    categories = coin['categories']
    #todo: take most popular sector to achieve biggest groups
    if type(categories) is list:
        if len(categories) > 0:
            sector = categories[0]
        else:
            sector = 'None'
    else:
        raise NotImplementedError
    coin_info.append(sector)

    coin_info.append(coin['genesis_date'])
    coin_info.append(coin['market_cap_rank'])
    coin_info.append(str(coin['hashing_algorithm']))
    coin_info.append(coin['coingecko_rank'])
    coin_info.append(coin['coingecko_score'])
    coin_info.append(coin['developer_score'])
    coin_info.append(coin['community_score'])
    coin_info.append(coin['liquidity_score'])
    coin_info.append(coin['public_interest_score'])
    market.append(coin_info)
    time.sleep(random.randint(0, 5))
    
market_df = pd.DataFrame(market, columns = ['id', 'symbol', 'name', 'sector', 'genesis_date',
                                            'market_cap_rank', 'hashing_algorithm', 
                                            'coingecko_rank', 'coingecko_score', 'developer_score', 'community_score', 
                                            'liquidity_score', 'public_interest_score'])
    
market_df['genesis_date'] = pd.to_datetime(market_df['genesis_date'])
market_df['base'] = 'usd'

100%|██████████| 100/100 [05:46<00:00,  3.47s/it]


In [71]:
market_df['ticker'] = market_df['symbol'] + '-' + market_df['base']

In [72]:
# combine the information into the market

market = top_100_coins_df.merge(market_df, on='id')

market.set_index(['ticker', 'symbol', 'base'], inplace=True)

In [73]:
# todo figure out why name and hasing algorithm are object and not string
market.info()
market['name'] = market['name'].astype(str)
market['hashing_algorithm'] = market['hashing_algorithm'].astype(str)
market

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 100 entries, ('btc-usd', 'btc', 'usd') to ('uma-usd', 'uma', 'usd')
Data columns (total 13 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     100 non-null    object        
 1   market_cap             100 non-null    int64         
 2   name                   100 non-null    object        
 3   sector                 100 non-null    object        
 4   genesis_date           36 non-null     datetime64[ns]
 5   market_cap_rank        100 non-null    int64         
 6   hashing_algorithm      100 non-null    object        
 7   coingecko_rank         100 non-null    int64         
 8   coingecko_score        100 non-null    float64       
 9   developer_score        100 non-null    float64       
 10  community_score        100 non-null    float64       
 11  liquidity_score        100 non-null    float64       
 12  public_interest_sc

In [74]:
market.head(10)

id    market_cap          name  \
ticker   symbol base                                            
btc-usd  btc    usd       bitcoin  682679851722       Bitcoin   
eth-usd  eth    usd      ethereum  300095281756      Ethereum   
usdt-usd usdt   usd        tether   62504685844        Tether   
ada-usd  ada    usd       cardano   56026875934       Cardano   
bnb-usd  bnb    usd   binancecoin   54658248672  Binance Coin   
xrp-usd  xrp    usd        ripple   46561225148           XRP   
doge-usd doge   usd      dogecoin   42100763541      Dogecoin   
usdc-usd usdc   usd      usd-coin   22772493359      USD Coin   
dot-usd  dot    usd      polkadot   22488657387      Polkadot   
uni-usd  uni    usd       uniswap   13916014794       Uniswap   

                                                  sector genesis_date  \
ticker   symbol base                                                    
btc-usd  btc    usd                       Cryptocurrency   2009-01-03   
eth-usd  eth    usd              Smart Contract Platform   2015-07-30   
usdt-usd usdt   usd                       USD Stablecoin          NaT   
ada-usd  ada    usd              Smart Contract Platform          NaT   
bnb-usd  bnb    usd     Centralized Exchange Token (CEX)   2017-07-08   
xrp-usd  xrp    usd                       Cryptocurrency          NaT   
doge-usd doge   usd                          Meme Tokens   2013-12-08   
usdc-usd usdc   usd                       USD Stablecoin          NaT   
dot-usd  dot    usd                   Polkadot Ecosystem          NaT   
uni-usd  uni    usd   Decentralized Exchange Token (DEX)          NaT   

                      market_cap_rank hashing_algorithm  coingecko_rank  \
ticker   symbol base                                                      
btc-usd  btc    usd                 1           SHA-256               1   
eth-usd  eth    usd                 2            Ethash               2   
usdt-usd usdt   usd                 3              None             151   
ada-usd  ada    usd                 4              None               6   
bnb-usd  bnb    usd                 5              None               4   
xrp-usd  xrp    usd                 6              None               7   
doge-usd doge   usd                 7            Scrypt               3   
usdc-usd usdc   usd                 8              None              69   
dot-usd  dot    usd                 9              None             138   
uni-usd  uni    usd                10              None             147   

                      coingecko_score  developer_score  community_score  \
ticker   symbol base                                                      
btc-usd  btc    usd            80.951          104.120           68.179   
eth-usd  eth    usd            78.586          101.988           61.187   
usdt-usd usdt   usd            41.949            0.000           10.798   
ada-usd  ada    usd            66.842           73.929           59.767   
bnb-usd  bnb    usd            69.207           77.124           63.641   
xrp-usd  xrp    usd            65.797           74.866           53.628   
doge-usd doge   usd            72.093           85.091           74.352   
usdc-usd usdc   usd            50.464           65.865            0.000   
dot-usd  dot    usd            42.887            0.000           44.345   
uni-usd  uni    usd            42.133            0.000           46.714   

                      liquidity_score  public_interest_score  
ticker   symbol base                                          
btc-usd  btc    usd            99.515                  0.383  
eth-usd  eth    usd           100.976                  0.472  
usdt-usd usdt   usd           106.694                  0.067  
ada-usd  ada    usd            85.253                  0.301  
bnb-usd  bnb    usd            85.361                 14.504  
xrp-usd  xrp    usd            86.136                  0.175  
doge-usd doge   usd            82.446                  0.208  
usdc

In [75]:
market.index.tolist

<bound method IndexOpsMixin.tolist of MultiIndex([(     'btc-usd',      'btc', 'usd'),
            (     'eth-usd',      'eth', 'usd'),
            (    'usdt-usd',     'usdt', 'usd'),
            (     'ada-usd',      'ada', 'usd'),
            (     'bnb-usd',      'bnb', 'usd'),
            (     'xrp-usd',      'xrp', 'usd'),
            (    'doge-usd',     'doge', 'usd'),
            (    'usdc-usd',     'usdc', 'usd'),
            (     'dot-usd',      'dot', 'usd'),
            (     'uni-usd',      'uni', 'usd'),
            (     'icp-usd',      'icp', 'usd'),
            (    'link-usd',     'link', 'usd'),
            (     'bch-usd',      'bch', 'usd'),
            (     'ltc-usd',      'ltc', 'usd'),
            (   'matic-usd',    'matic', 'usd'),
            (     'xlm-usd',      'xlm', 'usd'),
            (    'busd-usd',     'busd', 'usd'),
            (     'sol-usd',      'sol', 'usd'),
            (     'etc-usd',      'etc', 'usd'),
            (     'vet-usd',   

## Create categorical data from raw data and store in seperate data frame

In [76]:
def categorical_dict_to_np(cat_dict, unique_cats):
    # create array of symbols and categoricals 
    cat_np = np.zeros((len(cat_dict), len(unique_cats)), dtype=int)
    for ii, [key, values] in enumerate(cat_dict.items()): 
        for value in values: 
            idx = np.where(unique_cats == value)
            # print("{} is on idx {}".format(value, idx))
            cat_np[ii][idx] = 1
        assert(np.sum(cat_np[ii]) == len(values))
    return cat_np


def create_cat_dict(raw_data): 
    cat_dict = {}
    cat_list = []
    symbols = []
    max_len_cat = 0
    for coin in raw_data:
        categories = coin['categories']
        symbol = coin['symbol']
        cat_dict[symbol] = categories
        cat_list.extend(categories)
        symbols.append(symbol)
        max_len_cat = max(max_len_cat, len(coin['categories']))
    
    unique_cats = np.unique(cat_list)

    return cat_dict, unique_cats, symbols,

def categoricals_from_raw_coingecko(raw_data): 
    cat_dict, unique_cats, symbols = create_cat_dict(raw_data)

    cat_np = categorical_dict_to_np(cat_dict, unique_cats)
    
    cat_df = pd.DataFrame(cat_np, columns=unique_cats)
    cat_df['symbol'] = symbols
    cat_df['base'] = 'usd'
    cat_df['ticker'] = cat_df['symbol'] + '-' + cat_df['base']

    cat_df.set_index(['ticker', 'symbol', 'base'], inplace=True)
    print(unique_cats)
    print(cat_dict)
    return cat_df
    
cat_df = categoricals_from_raw_coingecko(raw_data)
cat_df

['Analytics' 'Artificial Intelligence' 'Asset-backed Tokens'
 'Automated Market Maker (AMM)' 'Avalanche Ecosystem'
 'Binance Smart Chain Ecosystem' 'Business Platform' 'Business Services'
 'Centralized Exchange Token (CEX)' 'Communication' 'Compound Tokens'
 'Cosmos Ecosystem' 'Cryptocurrency' 'Decentralized Exchange Token (DEX)'
 'Decentralized Finance (DeFi)' 'Derivatives' 'Entertainment'
 'Eth 2.0 Staking' 'Exchange-based Tokens' 'Finance / Banking' 'Gaming'
 'Governance' 'Infrastructure' 'Internet of Things (IOT)'
 'Lending/Borrowing' 'Masternodes' 'Meme Tokens' 'Metaverse'
 'Near Protocol Ecosystem' 'Non-Fungible Tokens (NFT)' 'Oracle'
 'Polkadot Ecosystem' 'Polygon Ecosystem' 'Privacy Coins' 'Protocol'
 'Seigniorage' 'Smart Contract Platform' 'Solana Ecosystem' 'Sports'
 'Stablecoins' 'Storage' 'Synthetic Issuer' 'Terra Ecosystem'
 'Tokenized BTC' 'USD Stablecoin' 'Wrapped-Tokens' 'Yearn Ecosystem'
 'Yield Aggregator' 'Yield Farming' 'xDAI Ecosystem']
{'btc': ['Cryptocurrency'], 

Analytics  Artificial Intelligence  \
ticker     symbol base                                       
btc-usd    btc    usd           0                        0   
eth-usd    eth    usd           0                        0   
usdt-usd   usdt   usd           0                        0   
ada-usd    ada    usd           0                        0   
bnb-usd    bnb    usd           0                        0   
...                           ...                      ...   
xsushi-usd xsushi usd           0                        0   
husd-usd   husd   usd           0                        0   
arrr-usd   arrr   usd           0                        0   
sc-usd     sc     usd           0                        0   
uma-usd    uma    usd           0                        0   

                        Asset-backed Tokens  Automated Market Maker (AMM)  \
ticker     symbol base                                                      
btc-usd    btc    usd                     0                             0   
eth-usd    eth    usd                     0                             0   
usdt-usd   usdt   usd                     0                             0   
ada-usd    ada    usd                     0                             0   
bnb-usd    bnb    usd                     0                             0   
...                                     ...                           ...   
xsushi-usd xsushi usd                     0                             0   
husd-usd   husd   usd                     0                             0   
arrr-usd   arrr   usd                     0                             0   
sc-usd     sc     usd                     0                             0   
uma-usd    uma    usd                     0                             0   

                        Avalanche Ecosystem  Binance Smart Chain Ecosystem  \
ticker     symbol base                                                       
btc-usd    btc    usd                     0                              0   
eth-usd    eth    usd                     0                              0   
usdt-usd   usdt   usd                     0                              0   
ada-usd    ada    usd                     0                              0   
bnb-usd    bnb    usd                     0                              1   
...                                     ...                            ...   
xsushi-usd xsushi usd                     0                              0   
husd-usd   husd   usd                     0                              0   
arrr-usd   arrr   usd                     0                              0   
sc-usd     sc     usd                     0                              0   
uma-usd    uma    usd                     0                              0   

                        Business Platform  Business Services  \
ticker     symbol base                                         
btc-usd    btc    usd                   0                  0   
eth-usd    eth    usd                   0                  0   
usdt-usd   usdt   usd                   0                  0   
ada-usd    ada    usd                   0                  0   
bnb-usd    bnb    usd                   0                  0   
...                                   ...                ...   
xsushi-usd xsushi usd                   0                  0   
husd-usd   husd   usd                   0                  0   
arrr-usd   arrr   usd                   0                  0   
sc-usd     sc     usd                   0                  0   
uma-usd    uma    usd                   0                  1   

                        Centralized Exchange Token (CEX)  Communication  ...  \
ticker     symbol base                                                   ...   
btc-usd    btc    usd                                  0              0  ...   
eth-usd    eth    usd                                  0              0  ...   
usdt-usd   usdt   usd                          

In [77]:
DATA_STORE = '../data/crypto.h5'
with pd.HDFStore(DATA_STORE) as store:
    store.put('coingecko/top100/market', market)
    store.put('coingecko/top100/cats', cat_df)
print("done")

done


In [78]:
raw_data


[{'id': 'bitcoin',
  'symbol': 'btc',
  'name': 'Bitcoin',
  'asset_platform_id': None,
  'platforms': {'': ''},
  'block_time_in_minutes': 10,
  'hashing_algorithm': 'SHA-256',
  'categories': ['Cryptocurrency'],
  'public_notice': None,
  'additional_notices': [],
  'description': {'en': 'Bitcoin is the first successful internet money based on peer-to-peer technology; whereby no central bank or authority is involved in the transaction and production of the Bitcoin currency. It was created by an anonymous individual/group under the name, Satoshi Nakamoto. The source code is available publicly as an open source project, anybody can look at it and be part of the developmental process.\r\n\r\nBitcoin is changing the way we see money as we speak. The idea was to produce a means of exchange, independent of any central authority, that could be transferred electronically in a secure, verifiable and immutable way. It is a decentralized peer-to-peer internet currency making mobile payment easy